![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Ekstrakcja informacji </h1>
<h2> 11. <i>NER RNN</i>  [ćwiczenia]</h2> 
<h3> Jakub Pokrywka (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

### Podejście softmax z embeddingami na przykładzie NER

In [1]:
import numpy as np
import torch
import pandas as pd

from datasets import load_dataset
import torchtext
#from torchtext.vocab import vocab
from collections import Counter


from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score

from tqdm.notebook import tqdm

import torch

In [2]:
device = 'cpu'

In [3]:
dataset = load_dataset("conll2003")

Reusing dataset conll2003 (/home/kuba/.cache/huggingface/datasets/conll2003/conll2003/1.0.0/63f4ebd1bcb7148b1644497336fd74643d4ce70123334431a3c053b7ee4e96ee)


  0%|          | 0/3 [00:00<?, ?it/s]

In [4]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    vocab = torchtext.vocab.vocab(counter, specials=['<unk>', '<pad>', '<bos>', '<eos>'])
    vocab.set_default_index(0)
    return vocab

In [5]:
vocab = build_vocab(dataset['train']['tokens'])

In [6]:
vocab['on']

21

In [7]:
def data_process(dt):
    return [ torch.tensor([vocab['<bos>']] +[vocab[token]  for token in  document ] + [vocab['<eos>']], dtype = torch.long) for document in dt]

In [8]:
def labels_process(dt):
    return [ torch.tensor([0] + document + [0], dtype = torch.long) for document in dt]


In [9]:
train_tokens_ids = data_process(dataset['train']['tokens'])

In [10]:
test_tokens_ids = data_process(dataset['test']['tokens'])

In [11]:
validation_tokens_ids =  data_process(dataset['validation']['tokens'])

In [12]:
train_labels = labels_process(dataset['train']['ner_tags'])

In [13]:
validation_labels = labels_process(dataset['validation']['ner_tags'])

In [14]:
test_labels = labels_process(dataset['test']['ner_tags'])

In [15]:
train_tokens_ids[0]

tensor([ 2,  4,  5,  6,  7,  8,  9, 10, 11, 12,  3])

In [16]:
dataset['train'][0]

{'id': '0',
 'tokens': ['EU',
  'rejects',
  'German',
  'call',
  'to',
  'boycott',
  'British',
  'lamb',
  '.'],
 'pos_tags': [22, 42, 16, 21, 35, 37, 16, 21, 7],
 'chunk_tags': [11, 21, 11, 12, 21, 22, 11, 12, 0],
 'ner_tags': [3, 0, 7, 0, 0, 0, 7, 0, 0]}

In [17]:
train_labels[0]

tensor([0, 3, 0, 7, 0, 0, 0, 7, 0, 0, 0])

In [18]:
def get_scores(y_true, y_pred):
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0 

    for p,t in zip(y_pred, y_true):
        if p == t:
            acc_score +=1

        if p > 0 and p == t:
            tp +=1

        if p > 0:
            selected_items += 1

        if t > 0 :
            relevant_items +=1

            
            
    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items
        
            
    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items
    
    
    if precision + recall == 0.0 :
        f1 = 0.0
    else:
        f1 = 2* precision * recall  / (precision + recall)

    return precision, recall, f1

In [19]:
num_tags = max([max(x) for x in dataset['train']['ner_tags'] if x]) + 1 

In [20]:
class LSTM(torch.nn.Module):

    def __init__(self):
        super(LSTM, self).__init__()
        self.emb = torch.nn.Embedding(len(vocab.get_itos()),100)
        self.rec = torch.nn.LSTM(100, 256, 1, batch_first = True)
        self.fc1 = torch.nn.Linear( 256 , 9)

    def forward(self, x):
        emb = torch.relu(self.emb(x))
        
        lstm_output, (h_n, c_n) = self.rec(emb)
        
        out_weights = self.fc1(lstm_output)

        return out_weights

In [21]:
lstm = LSTM().to(device)

In [22]:
criterion = torch.nn.CrossEntropyLoss().to(device)

In [23]:
optimizer = torch.optim.Adam(lstm.parameters())

In [24]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0).to(device)
        tags = list(dataset_labels[i].numpy())
        Y_true += tags
        
        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights,1)
        Y_pred += list(Y_batch_pred.cpu().numpy())
        

    return get_scores(Y_true, Y_pred)
        

In [25]:
NUM_EPOCHS = 5

In [26]:
for i in range(NUM_EPOCHS):
    lstm.train()
    #for i in tqdm(range(5000)):
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0).to(device)
        tags = train_labels[i].unsqueeze(1).to(device)
        
        
        predicted_tags = lstm(batch_tokens)

        
        optimizer.zero_grad()
        loss  = criterion(predicted_tags.squeeze(0),tags.squeeze(1))
        
        loss.backward()
        optimizer.step()
        
    lstm.eval()
    print(eval_model(validation_tokens_ids, validation_labels, lstm))

  0%|          | 0/14042 [00:00<?, ?it/s]

  0%|          | 0/3251 [00:00<?, ?it/s]

(0.516575591985428, 0.49447867023131464, 0.505285663380449)


  0%|          | 0/14042 [00:00<?, ?it/s]

  0%|          | 0/3251 [00:00<?, ?it/s]

...

  0%|          | 0/3251 [00:00<?, ?it/s]

(0.7282225874618455, 0.7210275485295827, 0.7246072075229251)


  0%|          | 0/14042 [00:00<?, ?it/s]

  0%|          | 0/3251 [00:00<?, ?it/s]

(0.7124554367201426, 0.7433453446472161, 0.7275726719381079)


In [27]:
eval_model(validation_tokens_ids, validation_labels, lstm)

  0%|          | 0/3251 [00:00<?, ?it/s]

(0.7124554367201426, 0.7433453446472161, 0.7275726719381079)

In [28]:
eval_model(test_tokens_ids, test_labels, lstm)

  0%|          | 0/3454 [00:00<?, ?it/s]

(0.6445353594389246, 0.6797337278106509, 0.6616667666646667)

In [29]:
len(train_tokens_ids)

14042

## pytania

- co zrobić z trenowaniem na batchach > 1 ?
- co zrobić, żeby sieć uwzględniała następne tokeny, a nie tylko poprzednie?
- w jaki sposób wykorzystać taką sieć do zadania zwykłej klasyfikacji?

### Zadanie na zajęcia ( 20 minut)

zmodyfikować sieć tak, żeby była używała dwuwarstwowej, dwukierunkowej warstwy GRU oraz dropoutu. Dropout ma nałożony na embeddingi.


## Zadanie domowe


- stworzyć model seq labelling bazujący na sieci neuronowej opisanej w punkcie niżej (można bazować na tym jupyterze lub nie).
- model sieci to GRU (o dowolnych parametrach) + CRF w pytorchu korzystając z modułu CRF z poprzednich zajęć- - stworzyć predykcje w plikach dev-0/out.tsv oraz test-A/out.tsv
- wynik fscore sprawdzony za pomocą narzędzia geval (patrz poprzednie zadanie) powinien wynosić conajmniej 0.65
termin 22.06, 60 punktów, za najlepszy wynik- 100 punktów
 